# SDV Evaluation notebook

**Welcome to the SDMetrics library!** SDMetrics (Synthetic Data Metrics) is an open source Python library for evaluating synthetic data.

In this notebook, we compare some real and synthetic demo data using SDMetrics. Along the way, we'll generate a shareable report, use it to discover some insights and create visual graphic

For more information about the library visit the [documentation website](https://docs.sdv.dev/sdmetrics/).

To connect with the community, [join their Slack channel](https://bit.ly/sdv-slack-invite).

# Installing SDMetrics

You can get started with SDMetrics by running the code in this notebook. SDMetrics is available under the MIT License.

The command belows will install the latest `sdmetrics` and other required Python packages.

In [ ]:
# versions of libraries in this notebook
# mysql-connector-python>=9.3.0
# pandas>=2.2.3
# plotly>=6.0.1
# pyhive>=0.7.0
# pyodbc>=5.2.0
# sdmetrics>=0.20.1
# sdv>=1.20.1
# sqlalchemy>=2.0.41

In [ ]:
%pip install sdmetrics==0.20.1
%pip install pyodbc==5.2.0
%pip install mysql-connector-python==9.3.0
%pip install sqlalchemy==2.0.41
%pip install pandas==2.2.3
%pip install sdv==1.20.1
%pip install pyhive==0.7.0
%pip install plotly==6.0.1

In [ ]:
import sdv
import sdmetrics
from sqlalchemy import create_engine
import pandas as pd
from sdmetrics.visualization import get_column_plot

## Option 1: Connect to your Database

In [ ]:
# Update database connection configuration as required
db_username = '<USERNAME>'
db_password = '<PASSWORD>'
db_host = '<HOST>'
db_port = '<PORT>'
original_db_name = '<SOURCE_DB_NAME>'
synthetic_db_name = '<DESTINATION_DB_NAME>'

# name of the schema and table in the source database
original_schema_name = None
original_table_name = "<TABLE_1>"
original_table_name_2 = "<TABLE_2>"

# name of the schema and table in the synthetic database
synthetic_schema_name = None
synthetic_table_name = "<TABLE_1>"
synthetic_table_name_2 = "<TABLE_2>"

### Connect to your source and destination data
**Attention**: The example below is specifix to MySQL case. Please refer to the SQL Alchemy documnetation for how to connect to other databases.

In [ ]:
# Create a SQLAlchemy connection to source data (examples for MySQL)
source_connection_str = f"mysql+mysqlconnector://{db_username}:{db_password}@{db_host}:{db_port}/{original_db_name}"
# source_connection_str = f"mssql+pyodbc://{db_username}:{db_password}@{db_host}:{db_port}/{original_db_name}?driver=ODBC+Driver+17+for+SQL+Server"
source_engine = create_engine(source_connection_str, echo=False)

# Create a SQLAlchemy connection to destination data (examples for MySQL and SQL Server)
destination_connection_str = f"mysql+mysqlconnector://{db_username}:{db_password}@{db_host}:{db_port}/{synthetic_db_name}"
# destination_connection_str = f"mssql+pyodbc://{db_username}:{db_password}@{db_host}:{db_port}/{synthetic_db_name}?driver=ODBC+Driver+17+for+SQL+Server"
destination_engine = create_engine(destination_connection_str, echo=False)

# Load table into DataFrame (examples with and without schema name)
train_df = pd.read_sql(f'SELECT * FROM {original_table_name}', source_engine)
synthetic_df = pd.read_sql(f'SELECT * FROM {synthetic_table_name}', destination_engine)
# train_df = pd.read_sql(f'SELECT * FROM {original_schema_name}.{original_table_name}', source_engine)
# synthetic_df = pd.read_sql(f'SELECT * FROM {synthetic_schema_name}.{synthetic_table_name}', destination_engine)
train_df_2 = pd.read_sql(f'SELECT * FROM {original_table_name_2}', source_engine)
synthetic_df_2 = pd.read_sql(f'SELECT * FROM {synthetic_table_name_2}', destination_engine)

# Display the DataFrame
train_df.head()

In [ ]:
# Drop PII columns (e.g. person names, SSNs, phone numbers), if present
train_df.drop(columns=['nameFirst', 'nameLast'], inplace=True)
synthetic_df.drop(columns=['nameFirst', 'nameLast'], inplace=True)

In [ ]:
# ensure data types are matching
inferred_dtypes_dict = train_df.dtypes.to_dict()
synthetic_df = synthetic_df.astype(inferred_dtypes_dict)

In [ ]:
from sdv.metadata import SingleTableMetadata

metadata = SingleTableMetadata()
metadata.detect_from_dataframe(data=train_df)
metadata = metadata.to_dict()

train_df = train_df.infer_objects()
synthetic_df = synthetic_df.infer_objects()
metadata

## Option 2: Load data from CSV

In [ ]:
from sdv.metadata import SingleTableMetadata

train_df = pd.read_csv("path/original-data.csv")
metadata = SingleTableMetadata()
metadata.detect_from_dataframe(data=train_df)
metadata = metadata.to_dict()

synthetic_df = pd.read_csv("path/synthetic-data.csv")
metadata

## Option 3: Load SDMetrics demo data

In [ ]:
from sdmetrics import load_demo

train_df, synthetic_df, metadata = load_demo(modality='single_table')

# Diagnostics report


The [Diagnostic Report](https://docs.sdv.dev/sdmetrics/reports/diagnostic-report/single-table-api#generate-real_data-synthetic_data-metadata) runs some basic checks on your synthetic data to give a general sense of the strengths and weakness of your synthetic data model.

In [ ]:
from sdmetrics.reports.single_table import DiagnosticReport

report = DiagnosticReport()

In [ ]:
report.generate(train_df, synthetic_df, metadata)

In [ ]:
# This method at any point retrieves each property that the report evaluated
# Returns: A dictionary that lists each property name and its associated score
report.get_properties()

In [ ]:
# 'Data Validity' shows the name of each individual column, the metric that was used to compute it and the overall score for that column.
report.get_details(property_name='Data Validity')

In [ ]:
# Optional: run this if you don't see any plots in the next steps
import plotly.io as pio

pio.renderers.default = 'iframe_connected'  # or 'colab' or 'iframe' or 'iframe_connected' or 'sphinx_gallery'

In [ ]:
report.get_visualization(property_name='Data Validity')

# Quality Report
The quality report measures statistical similarity between the real and synthetic data.

In [ ]:
from sdmetrics.reports.single_table import QualityReport

report = QualityReport()
report.generate(train_df, synthetic_df, metadata)

## Property: Column Shapes

This property looks at the overall shape the columns to see if the synthetic data matches the real data.

The report details indicate which columns have a better scores for this property. It also indicates which metric was used to compute the quality score (based on the data type).

In [ ]:
report.get_details(property_name='Column Shapes').head()

You can also visualize these scores.

In [ ]:
fig = get_column_plot(
    real_data=train_df,
    synthetic_data=synthetic_df,
    column_name='degree_perc',
)

fig.show()

We can look into specific columns by plotting them

In [ ]:
get_column_plot(
    real_data=train_df,
    synthetic_data=synthetic_df,
    column_name='duration',
)

## Property: Column Pair Trends
We can also compare the correlations between the real and synthetic data. The report can visualize the scores as a heatmap for easy inspection.

In [ ]:
report.get_visualization(property_name='Column Pair Trends')

The heatmap at the top shows the overall quality scores. The two heat maps at the bottom show a side-by-side comparison of the numerical columns for the real and synthetic data.

**Tip!** These headmaps are interactive. Hover and zoom for more details. You can also click the camera icon to save a picture.

In [ ]:
from sdmetrics.visualization import get_column_pair_plot

get_column_pair_plot(
    real_data=train_df,
    synthetic_data=synthetic_df,
    column_names=['degree_perc', 'high_perc'],
)

## Saving & Sharing

You can save the report object to share your insights with your team.

In [ ]:
# the report does not save the actual data but it does save metadata & scores
# this may still leak some privacy, so be careful when sharing your report!
report.save(filepath='sdmetrics_demo_quality_report.pkl')

# load the report at a later time
report = QualityReport.load(filepath='sdmetrics_demo_quality_report.pkl')

# Applying Individual Metrics

If you'd like to explore your data further, you can manually apply any of the [available metrics](https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary) in the library.

Let's also apply the `BoundaryAdherence` metric, which can be useful for applications like **software testing**. It tells us whether the synthetic data has respected the min/max boundaries of the real data.

In [ ]:
from sdmetrics.single_column import BoundaryAdherence

BoundaryAdherence.compute(
    train_df['mba_perc'],
    synthetic_df['mba_perc']
)

We can verify these findings by plotting the data.

In [ ]:
get_column_plot(
    real_data=train_df,
    synthetic_data=synthetic_df,
    column_name='mba_perc'
)

## Re-identification Risk
Likelihood of synthetic data still being identical or retraceable to PR data and to what degree this risk (if any) can be mitigated.

We can also check for **data privacy**. The `NewRowSynthesis` metric tells us whether the synthetic data contains any exact copies of the real data -- or whether the rows are new.

In [ ]:
from sdmetrics.single_table import NewRowSynthesis

nrs = NewRowSynthesis.compute(
    real_data=train_df,
    synthetic_data=synthetic_df,
    metadata=metadata
)
print(f'New Row Synthesis: {nrs}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/newrowsynthesis

## Other privacy metrics

### Metrics used: DCRBaselineProtection, DCROverfittingProtection and DisclosureProtection

The [DCRBaselineProtection](https://docs.sdv.dev/sdmetrics/metrics/privacy-metrics/dcrbaselineprotection) metric measures the distance between your synthetic data and real data to measure how private it is. For a fair measurement, it compares the distance against randomly generated data, which would provide the best possible privacy protection.

The [DCROverfittingProtection](https://docs.sdv.dev/sdmetrics/metrics/privacy-metrics/dcroverfittingprotection) metric measures the distance between your synthetic data and real training data to measure how private it is. It compares this against a validation set to determine the relative closeness.

The [DisclosureProtection](https://docs.sdv.dev/sdmetrics/metrics/privacy-metrics/disclosureprotection) metric measures the risk associated with disclosing (aka broadly sharing) the synthetic data. It's a useful measurement if you want to know whether synthetic data is leaking patterns that pertain to sensitive information.


In [ ]:
import pprint as pp

# DCRBaselineProtection
from sdmetrics.single_table import DCRBaselineProtection

dcr_baseline = DCRBaselineProtection.compute_breakdown(
    real_data=train_df,
    synthetic_data=synthetic_df,
    metadata=metadata
)
print(f'DCR Baseline Protection:')
pp.pp(dcr_baseline)
dcr_baseline = dcr_baseline["score"].item()

# DCROverfittingProtection
from sdmetrics.single_table import DCROverfittingProtection

# Requires a separate, holdout set of real data. This data should not have been used to train your synthesizer or create synthetic data.
# We'll just mimic this by splitting the original data into a training and holdout set.
holdout_df = train_df.sample(frac=0.5, random_state=42)
temp_train_df = train_df.drop(holdout_df.index)

dcr_overfitting = DCROverfittingProtection.compute_breakdown(
    real_training_data=temp_train_df,
    synthetic_data=synthetic_df,
    real_validation_data=holdout_df,
    metadata=metadata
)
print(f'DCR Overfitting Protection:')
pp.pp(dcr_overfitting)
dcr_overfitting = dcr_overfitting["score"].item()

# DisclosureProtection
from sdmetrics.single_table import DisclosureProtection

dp = DisclosureProtection.compute(
    real_data=train_df,
    synthetic_data=synthetic_df,
    known_column_names=['gender'],
    sensitive_column_names=['salary']
)
print(f'Disclosure Protection: {dp}')

## Preservation of relationships
Check if the relationships between tables and source systems (iSHS, Estate) remained intact after synthesizing the data (e.g. can loan numbers and other business keys still be related to each other?).
#### Used Methods: ReferentialIntegrity, CardinalityBoundaryAdherence, KeyUniquenes,   TableStructure


In [ ]:
# IMPORTANT: ReferentialIntegrity and CardinalityBoundaryAdherence can only be used if you connected to your own database and have two connected tables available.

# ReferentialIntegrity
from sdmetrics.column_pairs import ReferentialIntegrity

ri = ReferentialIntegrity.compute(
    real_data=(train_df['id'], train_df_2['players_id']),
    synthetic_data=(synthetic_df['id'], synthetic_df_2['players_id'])
)
print(f'Referential Integrity: {ri}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/referentialintegrity for more information&illustration for a multi table solution


# CardinalityBoundaryAdherence
from sdmetrics.column_pairs import CardinalityBoundaryAdherence

cba = CardinalityBoundaryAdherence.compute(
    real_data=(train_df['id'], train_df_2['players_id']),
    synthetic_data=(synthetic_df['id'], synthetic_df_2['players_id'])
)
print(f'Cardinality Boundary Adherence: {cba}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/cardinalityboundaryadherence for more information&illustration for a multi table solution

In [ ]:
# KeyUniqueness
# For columns that have a Mocker applied with Unique enabled, you can also run a KeyUniqueness to test if the column is unique

from sdmetrics.single_column import KeyUniqueness

ku = KeyUniqueness.compute(
    real_data=(train_df['student_id']),
    synthetic_data=(synthetic_df['student_id'])
)
print(f'Key Uniqueness: {ku}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/keyuniqueness for more information&illustration for a multi table solution

## TableStructure
from sdmetrics.single_table import TableStructure

ts = TableStructure.compute(
    real_data=train_df,
    synthetic_data=synthetic_df
)
print(f'Table Structure: {ts}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/tablestructure

## Preservation of data distribution 
Did the synthetically generated attributes contain a value distribution similar to the distribution within the original attributes (e.g. in terms of number of NULLs, unique values, outliers, etc).
#### Used Methods: CategoryCoverage, RangeCoverage, BoundaryAdherence, CategoryAdherence, MissingValueSimilarity, StatisticSimilarity

In [ ]:
## Category Coverage
from sdmetrics.single_column import CategoryCoverage

cc = CategoryCoverage.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary']
)
print(f'Category Coverage: {cc}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/categorycoverage

## Range Coverage
from sdmetrics.single_column import RangeCoverage

rc = RangeCoverage.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary']
)
print(f'Range Coverage: {rc}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/rangecoverage

## Boundary Adherence
from sdmetrics.single_column import BoundaryAdherence

ba = BoundaryAdherence.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary']
)
print(f'Boundary Adherence: {ba}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/boundaryadherence

## Category Adherence
from sdmetrics.single_column import CategoryAdherence

ca = CategoryAdherence.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary']
)
print(f'Category Adherence: {ca}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/categoryadherence

## Missing Value Similarity
from sdmetrics.single_column import MissingValueSimilarity

mvs = MissingValueSimilarity.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary']
)
print(f'Missing Value Similarity: {mvs}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/missingvaluesimilarity

## Statistic Similarity
from sdmetrics.single_column import StatisticSimilarity

ss = StatisticSimilarity.compute(
    real_data=train_df['salary'],
    synthetic_data=synthetic_df['salary'],
    statistic='mean' # can be mean, median and standard deviation
)
print(f'Statistic Similarity: {ss}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/statisticsimilarity

## Usability of the synthesized data
Was the attribute level data still recognizable (e.g. a name still looks like a name) and useful for its intended purpose (the dashboard)?

For example, for categorical columns (e.g. Gender, Country, ProductCode), CategoryCoverage will check the degree to which categories that exist in the original columns are also present in the AI-generated synthetic columns, which is key for the usability.

In [ ]:
## Category Coverage
from sdmetrics.single_column import CategoryCoverage

cc1 = CategoryCoverage.compute(
    real_data=train_df['gender'],
    synthetic_data=synthetic_df['gender']
)
cc2 = CategoryCoverage.compute(
    real_data=train_df['high_spec'],
    synthetic_data=synthetic_df['high_spec']
)
cc3 = CategoryCoverage.compute(
    real_data=train_df['degree_type'],
    synthetic_data=synthetic_df['degree_type']
)
print(f'Category Coverage: {cc1}')
print(f'Category Coverage: {cc2}')
print(f'Category Coverage: {cc3}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/categorycoverage

# Other Metrics
### Contingency Similarity and Correlation Similarity
Contingency Similarity computes the similarity of a pair of categorical columns between the real and synthetic datasets -- aka it compares 2D distributions.

Correlation Similarity measures the correlation between a pair of numerical columns and computes the similarity between the real and synthetic data -- aka it compares the trends of 2D distributions.

In [ ]:
## Contingency Similarity
from sdmetrics.column_pairs import ContingencySimilarity

cons = ContingencySimilarity.compute(
    real_data=train_df[['degree_perc', 'salary']],
    synthetic_data=synthetic_df[['degree_perc', 'salary']]
)
print(f'Contingency Similarity: {cons}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/metrics-glossary/contingencysimilarity

# Correlation Similarity
from sdmetrics.column_pairs import CorrelationSimilarity

cors = CorrelationSimilarity.compute(
    real_data=train_df[['degree_perc', 'salary']],
    synthetic_data=synthetic_df[['degree_perc', 'salary']],
    coefficient='Pearson'
)
print(f'Correlation Similarity: {cors}')
# Source: https://docs.sdv.dev/sdmetrics/metrics/quality-metrics/correlationsimilarity

# All metrics

In [ ]:
import plotly.graph_objects as go

# check if ri and cba exist, otherwise set them to None
if 'ri' not in locals():
    ri = None
    cba = None

# Data
metrics = ['New Row Synthesis', 'Referential Integrity', 'Cardinality Boundary Adherence', 'Key Uniqueness', 'Table Structure', 'Category Coverage', 'Range Coverage', 'Boundary Adherence', 'Category Adherence', 'Missing Value Similarity', 'Statistic Similarity', 'Category Coverage', 'Category Coverage', 'Category Coverage', 'Contingency Similarity', 'Correlation Similarity', 'DCR Baseline Protection', 'DCR Overfitting Protection', 'Disclosure Protection']
values = [nrs, ri, cba, ku, ts, cc, rc, ba, ca, mvs, ss, cc1, cc2, cc3, cons, cors, dcr_baseline, dcr_overfitting, dp]
column = ['all columns', 'id -> players_id', 'id -> players_id', 'student_id', 'table structure' 'salary', 'salary', 'salary', 'salary', 'salary', 'salary', 'gender', 'high_spec', 'degree_type', 'degree_perc&salary', 'degree_perc&salary', 'degree_perc&salary', 'all columns', 'all columns', 'all columns']

# Create an interactive table
fig = go.Figure(data=[go.Table(
    header=dict(values=['Metric', 'Value', 'Columns'],
                fill_color='paleturquoise',
                font=dict(color='black'),
                align='left'),
    cells=dict(values=[metrics, values, column],
               fill_color='lavender',
               font=dict(color='black'),
               align='left')

)
])

fig.show()